In [1]:
import pandas as pd
import numpy as np
import json
from datetime import datetime, timedelta
import matplotlib.pyplot as plt
pd.set_option('display.max_columns', None)
import seaborn as sns
from fim import arules

In [2]:
fact_table = pd.read_csv('fact_table.csv')

# Lets Explore and Understand the Data


In [3]:
# Sales Trends Over Time + line 
# product items
# top customers
# sales by location
# Payment Method Preferences
# Time of Day Analysis

In [4]:
fact_table

payment_key coustomer_key time_key item_key store_key  quantity   unit  \
0             P026       C004510  T049189   I00177    S00307         1     ct   
1             P022       C008967  T041209   I00248    S00595         1  rolls   
2             P030       C007261   T03633   I00195    S00496         8     ct   
3             P032       C007048  T084631   I00131     S0086         8     ct   
4             P014       C006430  T071276   I00050    S00488         8   cans   
...            ...           ...      ...      ...       ...       ...    ...   
999995        P010       C003726   T09247   I00063    S00502         5   cans   
999996        P021       C002581  T023483   I00252    S00225         1     ct   
999997        P035       C006133  T039372   I00119    S00555         7     ct   
999998        P031       C008735  T097975   I00257    S00440         2     ct   
999999        P032       C004067  T018028   I00044    S00326        10   cans   

        unit_price  total_price  
0             35.0         35.0  
1             26.0         26.0  
2             12.5        100.0  
3             14.0        112.0  
4              8.0         64.0  
...            ...          ...  
999995        40.0        200.0  
999996        11.0         11.0  
999997        53.0        371.0  
999998        21.0         42.0  
999999         8.0         80.0  

[1000000 rows x 9 columns]

In [5]:
item = pd.read_csv('item_dim.csv',  encoding='latin-1')

In [6]:
customer = pd.read_csv('customer_dim.csv', encoding='latin-1')

In [7]:
store = pd.read_csv('store_dim.csv', encoding='latin-1')

In [8]:
time_dim = pd.read_csv('time_dim.csv', encoding='latin-1')

In [9]:
trans = pd.read_csv('Trans_dim.csv', encoding='latin-1')

In [10]:
df = pd.merge(fact_table, time_dim, how='inner')

In [11]:
df = pd.merge(df, trans, how='inner')

In [12]:
df = pd.merge(df, store, how='inner')

In [13]:
df = pd.merge(df, item, how='inner')

In [14]:
df = pd.merge(df, customer, how='inner')
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1000000 entries, 0 to 999999
Data columns (total 28 columns):
 #   Column         Non-Null Count    Dtype  
---  ------         --------------    -----  
 0   payment_key    1000000 non-null  object 
 1   coustomer_key  1000000 non-null  object 
 2   time_key       1000000 non-null  object 
 3   item_key       1000000 non-null  object 
 4   store_key      1000000 non-null  object 
 5   quantity       1000000 non-null  int64  
 6   unit           996277 non-null   object 
 7   unit_price     1000000 non-null  float64
 8   total_price    1000000 non-null  float64
 9   date           1000000 non-null  object 
 10  hour           1000000 non-null  int64  
 11  day            1000000 non-null  int64  
 12  week           1000000 non-null  object 
 13  month          1000000 non-null  int64  
 14  quarter        1000000 non-null  object 
 15  year           1000000 non-null  int64  
 16  trans_type     1000000 non-null  object 
 17  bank_name

In [15]:
df.head()

payment_key coustomer_key time_key item_key store_key  quantity  unit  \
0        P026       C004510  T049189   I00177    S00307         1    ct   
1        P001       C004510  T082988   I00062    S00428        11  cans   
2        P018       C004510  T074754   I00196    S00378         8    ct   
3        P011       C004510   T06276   I00223    S00367         8    ct   
4        P034       C004510   T08402   I00229    S00535         9    ct   

   unit_price  total_price              date  hour  day      week  month  \
0        35.0         35.0  26-04-2016 17:13    17   26  4th Week      4   
1        37.0        407.0  11-05-2018 07:18     7   11  2nd Week      5   
2        16.0        128.0  29-11-2015 10:19    10   29  4th Week     11   
3        13.5        108.0  11-10-2016 23:06    23   11  2nd Week     10   
4        13.0        117.0  17-10-2017 23:17    23   17  3rd Week     10   

  quarter  year trans_type                   bank_name    division  \
0      Q2  2016       card        Premier Bank Limited       DHAKA   
1      Q2  2018       cash                        None  CHITTAGONG   
2      Q4  2015       card   Mutual Trust Bank Limited       DHAKA   
3      Q4  2016       card        Eastern Bank Limited       DHAKA   
4      Q4  2017       card  United Commercial Bank Ltd     BARISAL   

     district    upazila                            item_name  \
0    JAMALPUR   ISLAMPUR              M&M Peanut Candy 1.7 oz   
1  CHITTAGONG    ANOWARA                        Red Bull 16oz   
2     RAJBARI  KALUKHALI  Fiber One 90 Calorie Fudge Brownies   
3   NETRAKONA   BARHATTA         Lance Variety Cracker Packs    
4       BHOLA   LALMOHAN   Kellogg's Cereals Assortment Pack    

                        desc  man_country            supplier   name  \
0           Food - Chocolate  Netherlands     Bolsius Boxmeer  priya   
1  Beverage - Energy/Protein   Bangladesh        DENIMACH LTD  priya   
2             Food - Healthy       poland  CHROMADURLIN S.A.S  priya   
3              Food - Snacks   Bangladesh        DENIMACH LTD  priya   
4              Food - Sweets      Germany  Friedola 1888 GmbH  priya   

      contact_no            nid  
0  8801529462805  4543429591184  
1  8801529462805  4543429591184  
2  8801529462805  4543429591184  
3  8801529462805  4543429591184  
4  8801529462805  4543429591184

In [16]:
df['date'] = pd.to_datetime(df['date'])

In [17]:
df[df['unit'].isnull()].sort_values('item_key')

payment_key coustomer_key time_key item_key store_key  quantity unit  \
111           P010       C006906  T066216   I00158    S00205         9  NaN   
676431        P015       C004741  T072396   I00158    S00490        11  NaN   
676432        P035       C004741  T091436   I00158     S0072         3  NaN   
676536        P004       C002987  T082826   I00158    S00390        11  NaN   
676644        P033       C005485  T093362   I00158     S0078         4  NaN   
...            ...           ...      ...      ...       ...       ...  ...   
335774        P031       C009132   T05058   I00158    S00623         2  NaN   
335775        P010       C009132   T08139   I00158    S00601         2  NaN   
335883        P010       C003670  T063103   I00158    S00548         2  NaN   
332821        P010       C006242  T044473   I00158    S00190         9  NaN   
962793        P032       C000322  T039324   I00158    S00291         7  NaN   

        unit_price  total_price                date  hour  day      week  \
111           17.0        153.0 2016-07-08 00:26:00     0    7  1st Week   
676431        17.0        187.0 2018-04-09 22:59:00    22    4  1st Week   
676432        17.0         51.0 2017-12-22 19:35:00    19   22  4th Week   
676536        17.0        187.0 2019-06-09 19:20:00    19    6  1st Week   
676644        17.0         68.0 2017-07-01 04:39:00     4    7  1st Week   
...            ...          ...                 ...   ...  ...       ...   
335774        17.0         34.0 2018-06-17 20:57:00    20   17  3rd Week   
335775        17.0         34.0 2017-02-15 10:37:00    10   15  3rd Week   
335883        17.0         34.0 2016-09-08 20:54:00    20    9  2nd Week   
332821        17.0        153.0 2015-07-18 21:52:00    21   18  3rd Week   
962793        17.0        119.0 2020-06-29 18:46:00    18   29  4th Week   

        month quarter  year trans_type  \
111         8      Q3  2016       card   
676431      9      Q3  2018       card   
676432     12      Q4  2017       card   
676536      9      Q3  2019       card   
676644      1      Q1  2017       card   
...       ...     ...   ...        ...   
335774      6      Q2  2018       card   
335775      2      Q1  2017       card   
335883      8      Q3  2016       card   
332821      7      Q3  2015       card   
962793      6      Q2  2020       card   

                                                bank_name    division  \
111                             Dutch-Bangla Bank Limited      KHULNA   
676431                            Mercantile Bank Limited  CHITTAGONG   
676432                                Uttara Bank Limited     RANGPUR   
676536                                  Bank Asia Limited       DHAKA   
676644                                 Trust Bank Limited     RANGPUR   
...                                                   ...         ...   
335774                             Southeast Bank Limited       DHAKA   
335775                          Dutch-Bangla Bank Limited       DHAKA   
335883                          Dutch-Bangla Bank Limited     BARISAL   
332821                          Dutch-Bangla Bank Limited      KHULNA   
962793  South Bangla Agriculture and Commerce Bank Lim...       DHAKA   

            district           upazila                   item_name  \
111           KHULNA          PHULTALA  Frito Bold Flavors Variety   
676431  KHAGRACHHARI           RAMGARH  Frito Bold Flavors Variety   
676432   LALMONIRHAT           PATGRAM  Frito Bold Flavors Variety   
676536       SHERPUR     SHERPUR SADAR  Frito Bold Flavors Variety   
676644    NILPHAMARI   SAIDPUR UPAZILA  Frito Bold Flavors Variety   
...              ...               ...                         ...   
335774         DHAKA            KAFRUL  Frito Bold Flavors Variety   
335775         DHAKA       DARUS SALAM  Frito Bold Flavors Variety   
335883    PATUAKHALI  PATUAKHALI SADAR  Frito Bold Flavors Variety   
332821     JHENAIDAH   JHENAIDAH SADAR  Frito Bold Flavors Vari

In [18]:
item[item['item_key'] == 'I00158']

item_key                   item_name          desc  unit_price  \
157   I00158  Frito Bold Flavors Variety  Food - Chips        17.0   

    man_country  supplier unit  
157   Lithuania  BIGSO AB  NaN

In [19]:
df['unit'].fillna('Frito Bold Flavors Variety', inplace=True)

In [20]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1000000 entries, 0 to 999999
Data columns (total 28 columns):
 #   Column         Non-Null Count    Dtype         
---  ------         --------------    -----         
 0   payment_key    1000000 non-null  object        
 1   coustomer_key  1000000 non-null  object        
 2   time_key       1000000 non-null  object        
 3   item_key       1000000 non-null  object        
 4   store_key      1000000 non-null  object        
 5   quantity       1000000 non-null  int64         
 6   unit           1000000 non-null  object        
 7   unit_price     1000000 non-null  float64       
 8   total_price    1000000 non-null  float64       
 9   date           1000000 non-null  datetime64[ns]
 10  hour           1000000 non-null  int64         
 11  day            1000000 non-null  int64         
 12  week           1000000 non-null  object        
 13  month          1000000 non-null  int64         
 14  quarter        1000000 non-null  ob

# RFM Analysis

In [21]:
# create time_difference to capture part of data below
df["time_difference"] = df['date'].max() - df["date"]

In [22]:
#last two years
df["last_two_years"] = df["time_difference"] <= timedelta(days=2*365)

In [23]:
df_RFM = df[df['last_two_years']==True].copy()

In [24]:
df_RFM['Recency'] = (df_RFM['date'].max() - df_RFM['date']).dt.days


In [25]:
df_RFM.head()

payment_key coustomer_key time_key item_key store_key  quantity     unit  \
7         P039       C004510  T068435   I00141    S00591        11       ct   
28        P017       C004510  T068492   I00199    S00321        10       ct   
29        P018       C004510  T034129   I00194     S0039         7     bars   
35        P022       C004510  T034101   I00139    S00272         3       ct   
45        P010       C004510   T02137   I00042     S0084         7  bottles   

    unit_price  total_price                date  hour  day      week  month  \
7         18.0        198.0 2020-07-11 20:41:00    20    7  1st Week     11   
28        15.0        150.0 2020-08-22 12:23:00    12   22  4th Week      8   
29        23.0        161.0 2021-09-01 18:02:00    18    9  2nd Week      1   
35        24.0         72.0 2020-07-07 22:24:00    22    7  1st Week      7   
45        28.0        196.0 2020-12-18 15:32:00    15   18  3rd Week     12   

   quarter  year trans_type                  bank_name division     district  \
7       Q4  2020     mobile                      Nagad    DHAKA        DHAKA   
28      Q3  2020       card     Modhumoti Bank Limited    DHAKA  KISHOREGONJ   
29      Q1  2021       card  Mutual Trust Bank Limited  RANGPUR     DINAJPUR   
35      Q3  2020       card    NRB Commercial Bank Ltd    DHAKA        DHAKA   
45      Q4  2020       card  Dutch-Bangla Bank Limited  RANGPUR      RANGPUR   

         upazila                       item_name                         desc  \
7   BIMAN BANDAR  Hefty Cmprtmnt Plates Foam 10'            Dishware - Plates   
28     MITHAMAIN         Kellogg's Fruity Snacks               Food - Healthy   
29      BIRAMPUR  Detour Lower Sugar Protein Bar               Food - Healthy   
35         SAVAR     Foam Coffee Cups - 16 ounce          Dishware - Cups Hot   
45     BADARGANJ          Topo Chico 12 oz glass  a. Beverage Sparkling Water   

      man_country                        supplier   name     contact_no  \
7        Cambodia  NINGBO SEDUNO IMP & EXP CO.LTD  priya  8801529462805   
28      Lithuania                        BIGSO AB  priya  8801529462805   
29    Netherlands                 Bolsius Boxmeer  priya  8801529462805   
35        Germany              Friedola 1888 GmbH  priya  8801529462805   
45  United States                       MAESA SAS  priya  8801529462805   

              nid   time_difference  last_two_years  Recency  
7   4543429591184 508 days 02:17:00            True      508  
28  4543429591184 466 days 10:35:00            True      466  
29  4543429591184  91 days 04:56:00            True       91  
35  4543429591184 512 days 00:34:00            True      512  
45  4543429591184 348 days 07:26:00            True      348

### Using group by for each customer we need we create three now columns as following

 -Recency: for each customer snapshot date – latest purchase difference in days
 
 -Frequency: for each customer count of how many invoices are issued for him
 
 -Monetary Value: for each customer sum of amount spent

In [26]:
df_RFM = df_RFM.groupby(['coustomer_key']).agg({'Recency': np.min,
                                           'date':pd.Series.nunique,
                                           'total_price':np.sum}).reset_index()

df_RFM

coustomer_key  Recency  date  total_price
0          C000001        0     6       635.75
1          C000002      360    13      1134.25
2          C000003      398     8       669.25
3          C000004      345    17      1225.25
4          C000005      373    14      1427.75
...            ...      ...   ...          ...
9186       C009187      340    25      3024.25
9187       C009188      338    25      3152.00
9188       C009189      313    17      1424.00
9189       C009190      366    16      1898.75
9190       C009191       30    20      1930.00

[9191 rows x 4 columns]

In [27]:
#Rename columns
df_RFM.rename(columns={'Recency':'Recency','date':'Frequency','total_price':'Monetary'},inplace= True)

df_RFM

coustomer_key  Recency  Frequency  Monetary
0          C000001        0          6    635.75
1          C000002      360         13   1134.25
2          C000003      398          8    669.25
3          C000004      345         17   1225.25
4          C000005      373         14   1427.75
...            ...      ...        ...       ...
9186       C009187      340         25   3024.25
9187       C009188      338         25   3152.00
9188       C009189      313         17   1424.00
9189       C009190      366         16   1898.75
9190       C009191       30         20   1930.00

[9191 rows x 4 columns]

### We have now calculated our values. But those aggregations are absolut and hard to explain as is. It is better to normalize our scores replacing those values with relative once with respect to the distribution

### Pandas qcut splits numeric columns into quartiles.

### For Recency and Frequency columns, the higher values (top quartile) are assigned with indicator 4 and lowest to 1. Higher values imply that customers have spent more money to our products or bought more often and the 1-4 score is assigned accordingly

### The opposite logic is applied for recency as higher values mean that many days have passed since last purchase. Thus, customers with high values (top quartile) take score 1 and those with the smallest values 4.

In [28]:
# Create Scores RFM scores based on quantiles of distribution

#Date from customer's last purchase.The nearest date gets 4 and the furthest date gets 1.
df_RFM["recency_score"] = pd.qcut(df_RFM['Recency'].rank(method="first"),
                                  4,
                                  labels=[4, 3, 2, 1])

# Total number of purchases.The least frequency gets 1 and the maximum frequency gets 4.
df_RFM["frequency_score"] = pd.qcut(df_RFM["Frequency"].rank(method="first"),
                                    4,
                                    labels=[1, 2, 3, 4])

#Total spend by the customer.The least money gets 1, the most money gets 4.
df_RFM["monetary_score"] = pd.qcut(df_RFM["Monetary"].rank(method="first"),
                                   4,
                                   labels=[1, 2, 3, 4])

df_RFM.head()

coustomer_key  Recency  Frequency  Monetary recency_score frequency_score  \
0       C000001        0          6    635.75             4               1   
1       C000002      360         13   1134.25             1               1   
2       C000003      398          8    669.25             1               1   
3       C000004      345         17   1225.25             2               2   
4       C000005      373         14   1427.75             1               1   

  monetary_score  
0              1  
1              1  
2              1  
3              1  
4              1

## Calculate total RFM score for each customer


In [29]:
df_RFM["RFM_Segment"] = df_RFM["recency_score"].astype(str) + df_RFM[
    "frequency_score"].astype(str) + df_RFM["monetary_score"].astype(str)

df_RFM['RFM_Score'] = df_RFM[[
    'recency_score', 'frequency_score', 'monetary_score'
]].sum(axis=1)
df_RFM.head()

coustomer_key  Recency  Frequency  Monetary recency_score frequency_score  \
0       C000001        0          6    635.75             4               1   
1       C000002      360         13   1134.25             1               1   
2       C000003      398          8    669.25             1               1   
3       C000004      345         17   1225.25             2               2   
4       C000005      373         14   1427.75             1               1   

  monetary_score RFM_Segment  RFM_Score  
0              1         411          6  
1              1         111          3  
2              1         111          3  
3              1         221          5  
4              1         111          3

### Split customers to segments and give indicative names (labeling appoaches may vary for this step)


In [30]:
segt_map = {
    r'[3-4][3-4]4': 'VIP',
    r'[2-3-4][1-2-3-4]4': 'Top Recent',
    r'1[1-2-3-4]4': 'Top at Risk ',

    
    
    r'[3-4][3-4]3': 'High Promising',
    r'[2-3-4][1-2]3': 'High New',
    r'2[3-4]3': 'High Loyal',

    
    
    r'[3-4][3-4]2': 'Medium Potential',
    r'[2-3-4][1-2]2': 'Medium New',
    r'2[3-4]2': 'Medium Loyal',

    
    
    r'4[1-2-3-4]1': 'Low New',
    r'[2-3][1-2-3-4]1': 'Low Loyal',
    
    r'1[1-2-3-4][1-2-3]': 'Need Activation'
}
df_RFM['Segment_labels'] = df_RFM['RFM_Segment']
df_RFM['Segment_labels'] = df_RFM['Segment_labels'].replace(segt_map, regex=True)
df_RFM.head()

coustomer_key  Recency  Frequency  Monetary recency_score frequency_score  \
0       C000001        0          6    635.75             4               1   
1       C000002      360         13   1134.25             1               1   
2       C000003      398          8    669.25             1               1   
3       C000004      345         17   1225.25             2               2   
4       C000005      373         14   1427.75             1               1   

  monetary_score RFM_Segment  RFM_Score   Segment_labels  
0              1         411          6          Low New  
1              1         111          3  Need Activation  
2              1         111          3  Need Activation  
3              1         221          5        Low Loyal  
4              1         111          3  Need Activation

In [31]:
seg_pareto = df_RFM.groupby(["Segment_labels"]).agg({'Monetary': np.sum,
                 
                                                           "coustomer_key": pd.Series.nunique}).reset_index()

seg_pareto

Segment_labels    Monetary  coustomer_key
0         High Loyal   871837.00            430
1           High New  1108148.50            560
2     High Promising  1649330.50            817
3          Low Loyal  1284312.50           1078
4            Low New   535653.25            445
5       Medium Loyal   345367.00            207
6         Medium New  1733744.50           1067
7   Medium Potential   672448.50            401
8    Need Activation  2903612.50           1888
9         Top Recent  1615442.00            631
10      Top at Risk   1055017.75            410
11               VIP  3317708.50           1257

In [32]:
seg_pareto["Monetary%"] = seg_pareto["Monetary"]/seg_pareto["Monetary"].sum()
seg_pareto = seg_pareto.sort_values(by=['Monetary%'], ascending=False)
seg_pareto["CumulativePercentage"] = (seg_pareto["Monetary"].cumsum()/ 
                                      seg_pareto["Monetary"].sum()*100).round(2)
seg_pareto["CumulativeSum"] = (seg_pareto["coustomer_key"].cumsum()/ 
                                      seg_pareto["coustomer_key"].sum()*100).round(2)

seg_pareto

Segment_labels    Monetary  coustomer_key  Monetary%  \
11               VIP  3317708.50           1257   0.194102   
8    Need Activation  2903612.50           1888   0.169875   
6         Medium New  1733744.50           1067   0.101432   
2     High Promising  1649330.50            817   0.096494   
9         Top Recent  1615442.00            631   0.094511   
3          Low Loyal  1284312.50           1078   0.075138   
1           High New  1108148.50            560   0.064832   
10      Top at Risk   1055017.75            410   0.061724   
0         High Loyal   871837.00            430   0.051007   
7   Medium Potential   672448.50            401   0.039341   
4            Low New   535653.25            445   0.031338   
5       Medium Loyal   345367.00            207   0.020206   

    CumulativePercentage  CumulativeSum  
11                 19.41          13.68  
8                  36.40          34.22  
6                  46.54          45.83  
2                  56.19          54.72  
9                  65.64          61.58  
3                  73.16          73.31  
1                  79.64          79.40  
10                 85.81          83.86  
0                  90.91          88.54  
7                  94.85          92.91  
4                  97.98          97.75  
5                 100.00         100.00

# Market Basket Analysis


## Association Rules


In [33]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1000000 entries, 0 to 999999
Data columns (total 30 columns):
 #   Column           Non-Null Count    Dtype          
---  ------           --------------    -----          
 0   payment_key      1000000 non-null  object         
 1   coustomer_key    1000000 non-null  object         
 2   time_key         1000000 non-null  object         
 3   item_key         1000000 non-null  object         
 4   store_key        1000000 non-null  object         
 5   quantity         1000000 non-null  int64          
 6   unit             1000000 non-null  object         
 7   unit_price       1000000 non-null  float64        
 8   total_price      1000000 non-null  float64        
 9   date             1000000 non-null  datetime64[ns] 
 10  hour             1000000 non-null  int64          
 11  day              1000000 non-null  int64          
 12  week             1000000 non-null  object         
 13  month            1000000 non-null  int64   

## 1 - Produce an Association Rules Report which will show the below measures: 
### support itemset absolute, support itemset relative pct, confidence pct and lift

In [34]:
# inputs
supp = 10  # minimum support of an assoc. rule (default: 10)
conf = 50  # minimum confidence of an assoc. rule (default: 80%)
zmin = 2
zmax = 2
report = 'aSCl'

In [35]:
report_colnames = {
    'a': 'support_itemset_absolute',
    's': 'support_itemset_relative',
    'S': 'support_itemset_relative_pct',
    'b': 'support_bodyset_absolute',
    'x': 'support_bodyset_relative',
    'X': 'support_bodyset_relative_pct',
    'h': 'support_headitem_absolute',
    'y': 'support_headitem_relative',
    'Y': 'support_headitem_relative_pct',
    'c': 'confidence',
    'C': 'confidence_pct',
    'l': 'lift',
    'L': 'lift_pct',
    'e': 'evaluation',
    'E': 'evaluation_pct',
    'Q': 'support of the empty set (total number of transactions)'
    }

In [36]:
cust_prod=df.groupby('coustomer_key')['item_name'].apply(list)
cust_prod

coustomer_key
C000001    [Vita Coconut Water 10oz , Frito Big Grab Vari...
C000002    [M&M Peanut Candy 1.7 oz, Fiber One 90 Calorie...
C000003    [Frito Big Grab Variety 1.5-2.0 oz, Red Bull 1...
C000004    [Frito Big Grab Variety 1.5-2.0 oz, French Van...
C000005    [Vita Coconut Water 10oz , Red Bull 16oz, Mons...
                                 ...                        
C009187    [Red Bull 16oz, Frito Bold Flavors Variety, La...
C009188    [Kleenex Tissue Rectangle Boxes 160/box, Honey...
C009189    [Red Bull 16oz, Red Bull 16oz, Monster Zero Ul...
C009190    [M&M Peanut Candy 1.7 oz, Vita Coconut Water 1...
C009191    [Frito Big Grab Variety 1.5-2.0 oz, Frito Big ...
Name: item_name, Length: 9191, dtype: object

In [37]:
# Create list of lists to pass it into PyFim

cust_prod_list=cust_prod.to_list()
cust_prod_list

[['Vita Coconut Water 10oz ',
  'Frito Big Grab Variety 1.5-2.0 oz',
  'Red Bull 16oz',
  'Kleenex Tissue Rectangle Boxes 160/box',
  'Honey Packets  ',
  'Dixie Perfecttouch Paper Cups 12oz',
  "Kellogg's Cereals Assortment Pack ",
  "Hefty Cmprtmnt Plates Foam 10'",
  'Topo Chico 20oz plastic',
  'Sprite - 12 oz cans',
  'Clear Plastic Cups 9oz',
  'Lunchables Variety Pack Oscar Meyer',
  'Snapple Variety Pack 20oz',
  'Cliff Energy Bars Variety Pack',
  'Pop-Tarts, Frosted Strawberry',
  'Gatorade Zero Variety 20 oz',
  'Gatorade Zero Variety 20 oz',
  'Peanutbutter Filled Pretzels',
  'Cascade Gel w/ Dawn Dishwasher',
  'Hershey Kisses ',
  "Barq's Root Beer - 12 oz cans",
  "Barq's Root Beer - 12 oz cans",
  'Ozarka Spring Water 20 oz',
  'Jolly Ranchers Variety Hard Candy',
  'Famous Amos Cookies ',
  'Cherry Coke Zero 12 pack',
  'Gatorade Liberty Variety 12 oz',
  'Sugar in the Raw Packets',
  'Frito Classic Mix Variety',
  'Foam Coffee Cups - 16 ounce',
  'La Croix Sparkling G

In [38]:
# Run apriori algorithm to creeate associations
apriori = arules(cust_prod_list, supp=supp, conf=conf, report=report,eval='lift', zmin = 2,zmax = 2)

In [39]:
#Uncomment and run in case you want to see parameters of association rules
#??arules 


#Creat dataframe wiht columns based on the report variables and sorted based on the "Associations_Sorted_based_on"
colnames = ['Cons_Product', 'antecedent'] + [report_colnames.get(k, k) for k in list(report)]
df_rules = pd.DataFrame(apriori, columns=colnames)
df_rules = df_rules.sort_values(report_colnames["a"], ascending=False)

#Change order of columns antecedent and consequent
df_rules = df_rules[['antecedent', 'Cons_Product']+ [report_colnames.get(k, k) for k in list(report)]]


#Print the numbers of rules created
print(df_rules.shape)

#Print top 10 and last 10 rules (the last 10 will be shown)
df_rules

(1290, 6)


antecedent  \
0                      (Pepsi - 12 oz cans,)   
1                     (Sprite - 12 oz cans,)   
9                      (Pepsi - 12 oz cans,)   
8     (Muscle Milk Protein Shake Van. 11oz,)   
10    (Muscle Milk Protein Shake Van. 11oz,)   
...                                      ...   
1118        (Folgers 100% Colombian Coffee,)   
1274                (Monster Lo-Carb 16 oz,)   
1218            (Mountain Dew - 12 oz cans,)   
1014  (Ozarka Spring Water 16.9 oz bottles,)   
1237          (Zoo Animal Cookies/Crackers,)   

                             Cons_Product  support_itemset_absolute  \
0                     Sprite - 12 oz cans                      2981   
1                      Pepsi - 12 oz cans                      2981   
9     Muscle Milk Protein Shake Van. 11oz                      2921   
8                      Pepsi - 12 oz cans                      2921   
10                Coke Classic 12 oz cans                      2915   
...                                   ...                       ...   
1118  Muscle Milk Protein Shake Van. 11oz                      1648   
1274               Diet Coke - 12 oz cans                      1646   
1218  Muscle Milk Protein Shake Van. 11oz                      1644   
1014               Diet Coke - 12 oz cans                      1644   
1237              Coke Classic 12 oz cans                      1643   

      support_itemset_relative_pct  confidence_pct      lift  
0                        32.433903       57.348980  1.012475  
1                        32.433903       57.260853  1.012475  
9                        31.781090       56.194690  1.008564  
8                        31.781090       57.039641  1.008564  
10                       31.715809       56.922476  1.018047  
...                            ...             ...       ...  
1118                     17.930584       53.997379  0.969127  
1274                     17.908824       54.648074  0.984265  
1218                     17.887063       54.275338  0.974116  
1014                     17.887063       53.498210  0.963555  
1237                     17.876183       54.458071  0.973972  

[1290 rows x 6 columns]

## 2 - Find the Top5 Association in terms of Support Absolute, confidence and lift and provide an interpretation of your results for these product relations

In [40]:
df_rules = df_rules.sort_values(by='lift', ascending=False)
df_rules.head(30)

antecedent  \
1109              (Gatorade Frost Variety 12 oz,)   
1086                  (Clear Plastic 12 oz Cups,)   
480         (Tropicana Orange Juice 10 oz 100% ,)   
1191     (Coffee-mate Original Powdered Creamer,)   
602             (La Croix Sparkling Lemon 12 oz,)   
83                    (M&M Peanut Butter 1.6 oz,)   
922             (Lysol Disinfectant Spray 19 oz,)   
387                       (Advil 2 pill packets,)   
531          (Crunchy Granola Bars Oats & Honey,)   
154               (Cascade Gel Packs Dishwasher,)   
165                    (Gatorade Variety 20 oz ,)   
141           (Coffee-Mate Original Flavor Cold,)   
873                           (Gardettos Snacks,)   
860                   (Cheetos Flamin' Hot 1 oz,)   
1180                   (M&M Peanut Candy 1.7 oz,)   
187               (Pringles Snak Stacks Variety,)   
296               (Waterloo Sparkling Lime 12oz,)   
261             (Cascade Gel w/ Dawn Dishwasher,)   
391          (V8 100% Vegetable Juice 11oz cans,)   
953                (Sunkist Orange - 12 oz cans,)   
1034              (Diet Dr. Pepper - 12 oz cans,)   
1002                      (Tootsie Roll Midgets,)   
559             (K Cups  Starbuck's Pike Place,)   
365         (Breath Savers Peppermints 12/roll ,)   
1214  (Goldfish Variety Bags, cheddar, pretzels,)   
465    (Nabisco Cookie Variety Pk Oreo/ChocChip,)   
931               (Frito Fiesta Flavors Variety,)   
349         (Kellogg's Cereals Assortment Pack ,)   
1283          (Hefty Supreme Foam Plates 6 inch,)   
285            (Quaker Instant Oatmeal Variety ,)   

                             Cons_Product  support_itemset_absolute  \
1109               Diet Coke - 12 oz cans                      1783   
1086                   Pepsi - 12 oz cans                      1799   
480                   Sprite - 12 oz cans                      1827   
1191                   Pepsi - 12 oz cans                      1775   
602               Coke Classic 12 oz cans                      1790   
83    Muscle Milk Protein Shake Van. 11oz                      1823   
922               Coke Classic 12 oz cans                      1775   
387               Coke Classic 12 oz cans                      1805   
531                    Pepsi - 12 oz cans                      1818   
154                Diet Coke - 12 oz cans                      1808   
165                   Sprite - 12 oz cans                      1844   
141                    Pepsi - 12 oz cans                      1841   
873   Muscle Milk Protein Shake Van. 11oz                      1768   
860                   Sprite - 12 oz cans                      1796   
1180                  Sprite - 12 oz cans                      1773   
187               Coke Classic 12 oz cans                      1813   
296                    Pepsi - 12 oz cans                      1824   
261                    Pepsi - 12 oz cans                      1829   
391                    Pepsi - 12 oz cans                      1822   
953   Muscle Milk Protein Shake Van. 11oz                      1760   
1034               Diet Coke - 12 oz cans                      1746   
1002              Coke Classic 12 oz cans                      1764   
559                Diet Coke - 12 oz cans                      1771   
365                   Sprite - 12 oz cans                      1821   
1214               Diet Coke - 12 oz cans                      1726   
465                   Sprite - 12 oz cans                      1809   
931                    Pepsi - 12 oz cans                      1781   
349                Diet Coke - 12 oz cans                      1785   
1283  Muscle Milk Protein Shake Van. 11oz                      1714   
285                   Sprite - 12 oz cans                      1822   

      support_itemset_relative_pct  confidence_pct      lift  
1109                     19.399412       58.363339  1.051181  
1086                     19.573496       58.829300  1.040208  
480 

In [41]:
df_rules = df_rules.sort_values(by='confidence_pct', ascending=False)
df_rules.head(30)

antecedent            Cons_Product  \
1086                 (Clear Plastic 12 oz Cups,)      Pepsi - 12 oz cans   
480        (Tropicana Orange Juice 10 oz 100% ,)     Sprite - 12 oz cans   
1191    (Coffee-mate Original Powdered Creamer,)      Pepsi - 12 oz cans   
165                   (Gatorade Variety 20 oz ,)     Sprite - 12 oz cans   
1109             (Gatorade Frost Variety 12 oz,)  Diet Coke - 12 oz cans   
531         (Crunchy Granola Bars Oats & Honey,)      Pepsi - 12 oz cans   
860                  (Cheetos Flamin' Hot 1 oz,)     Sprite - 12 oz cans   
1180                  (M&M Peanut Candy 1.7 oz,)     Sprite - 12 oz cans   
141          (Coffee-Mate Original Flavor Cold,)      Pepsi - 12 oz cans   
296              (Waterloo Sparkling Lime 12oz,)      Pepsi - 12 oz cans   
261            (Cascade Gel w/ Dawn Dishwasher,)      Pepsi - 12 oz cans   
391         (V8 100% Vegetable Juice 11oz cans,)      Pepsi - 12 oz cans   
365        (Breath Savers Peppermints 12/roll ,)     Sprite - 12 oz cans   
465   (Nabisco Cookie Variety Pk Oreo/ChocChip,)     Sprite - 12 oz cans   
285           (Quaker Instant Oatmeal Variety ,)     Sprite - 12 oz cans   
931              (Frito Fiesta Flavors Variety,)      Pepsi - 12 oz cans   
865      (Half & Half -Land o Lakes Mini Moo's,)     Sprite - 12 oz cans   
1075   (Kleenex Tissue Rectangle Boxes 160/box,)     Sprite - 12 oz cans   
790                           (Hershey Nuggets,)     Sprite - 12 oz cans   
1265            (Dole Fruit in Gel Cups 4.3 oz,)     Sprite - 12 oz cans   
1165                (Snapple Variety Pack 20oz,)     Sprite - 12 oz cans   
1250           (Hefty Cmprtmnt Plates Foam 10',)     Sprite - 12 oz cans   
756         (Diet Coke Caffeine Free 12oz cans,)      Pepsi - 12 oz cans   
915                  (Cherry Coke Zero 12 pack,)     Sprite - 12 oz cans   
490                 (Diet Gingerale 12 oz cans,)     Sprite - 12 oz cans   
705                   (Flamin Hot Chip Mix 1oz,)     Sprite - 12 oz cans   
271            (Cliff Energy Bars Variety Pack,)      Pepsi - 12 oz cans   
1091            (La Croix Sparkling Pure 12 oz,)      Pepsi - 12 oz cans   
396             (Swiss Miss Hot Cocoa Mix 1 oz,)      Pepsi - 12 oz cans   
110                 (Doritos Nacho Cheese 1 oz,)     Sprite - 12 oz cans   

      support_itemset_absolute  support_itemset_relative_pct  confidence_pct  \
1086                      1799                     19.573496       58.829300   
480                       1827                     19.878142       58.520179   
1191                      1775                     19.312371       58.407371   
165                       1844                     20.063105       58.391387   
1109                      1783                     19.399412       58.363339   
531                       1818                     19.780220       58.362761   
860                       1796                     19.540855       58.311688   
1180                      1773                     19.290610       58.303190   
141                       1841                     20.030465       58.296390   
296                       1824                     19.845501       58.163265   
261                       1829                     19.899902       58.155803   
391                       1822                     19.823741       58.155123   
365                       1821                     19.812860       58.141762   
465                       1809                     19.682298       58.129820   
285                       1822                     19.823741       58.080969   
931                       1781                     19.377652       58.031932   
865                       1789                     19.464694       58.009079   
1075                      1776                     19.323251       58.001306   
790                       1791                     19.486454       57.998705   
1265                      1748                     19.018605       57.957560   
1

## 3 - Is there product cannibalization between products? If yes, provide for which products. If not, support your statement.

In [42]:
df_rules = df_rules.sort_values(by='lift', ascending=True)
df_rules.head(50)

antecedent  \
891           (Tejava Unsweetened Black Tea 16.9oz,)   
1014          (Ozarka Spring Water 16.9 oz bottles,)   
238      (Go-Gurt Low Fat Yogurt, Strwbry & Berry ,)   
996                  (Folgers Classic Roast Coffee,)   
652                   (Foam Coffee Cups - 16 ounce,)   
308              (Pop-Tarts, Brown Sugar Cinnamon ,)   
894           (Tejava Unsweetened Black Tea 16.9oz,)   
1266                (Dole Fruit in Gel Cups 4.3 oz,)   
995                  (Folgers Classic Roast Coffee,)   
1261                (Hershey Factory Favorites Mix,)   
491                     (Diet Gingerale 12 oz cans,)   
1118                (Folgers 100% Colombian Coffee,)   
533             (Crunchy Granola Bars Oats & Honey,)   
644                 (K Cups - McCafe Premium Roast,)   
63           (Nat.Valley PeanutButter Protein Bars,)   
1045              (La Croix Sparkling Orange 12 oz,)   
1053                      (Strong Everyday Napkins,)   
549            (Waterloo Sparkling Watermelon 12oz,)   
46     (Ocean Spray Cranberry Juice Cocktail 15oz ,)   
196                 (Baked Chips Variety Mix Frito,)   
649                   (Njoy Creamer Canister 16 oz,)   
375                      (Mars Chocolate Favorites,)   
588                    (M&M Variety Full Size Bags,)   
940                          (Famous Amos Cookies ,)   
774            (Perrier Sparkling Water glass 11oz,)   
1237                  (Zoo Animal Cookies/Crackers,)   
1218                    (Mountain Dew - 12 oz cans,)   
353                    (Planters Nut Variety Packs,)   
201           (La Croix Sparkling Grapefruit 12 oz,)   
693                     (Spunkmeyer Muffin Variety,)   
735                   (Stirrers Coffee Stirs 7inch,)   
406                (Reese's Peanutbutter Cups 2/pk,)   
595                              (Cherry Coke 12oz,)   
1020                            (Chex Mix Original,)   
628    (Dawn Ultra Dish Detergent, Original Scent ,)   
1177          (Waterloo Sparkling Blackcherry 12oz,)   
356            (Chobani Greek Yogurt Variety Pack ,)   
190        (Apple Sauce Variety GoGO Squeeze 3.2oz,)   
546            (Waterloo Sparkling Watermelon 12oz,)   
567                         (Seven Up - 12 oz cans,)   
1203            (Plastic Knives White  Heavyweight,)   
1033                 (Diet Dr. Pepper - 12 oz cans,)   
889                  (Dasani Bottled Water 16.9 oz,)   
163                  (Planters Nut-trition 1.5 oz ,)   
746                         (Nestle Purelife 16oz ,)   
424                 (Waterloo Sparkling Mango 12oz,)   
1105                 (Gatorade Frost Variety 12 oz,)   
877   (Nature Valley Sweet/Salty Peanut Bars      ,)   
1083           (Dixie Perfecttouch Paper Cups 12oz,)   
520         (Nature Valley Soft Oatmeal Squares   ,)   

                             Cons_Product  support_itemset_absolute  \
891                    Pepsi - 12 oz cans                      1679   
1014               Diet Coke - 12 oz cans                      1644   
238   Muscle Milk Protein Shake Van. 11oz                      1695   
996                    Pepsi - 12 oz cans                      1682   
652               Coke Classic 12 oz cans                      1681   
308   Muscle Milk Protein Shake Van. 11oz                      1693   
894                Diet Coke - 12 oz cans                      1661   
1266                   Pepsi - 12 oz cans                      1651   
995                   Sprite - 12 oz cans                      1686   
1261                   Pepsi - 12 oz cans                      1652   
491                    Pepsi - 12 oz cans                      1708   
1118  Muscle Milk Protein Shake Van. 11oz                      1648   
533   Muscle Milk Protein Shake Van. 11oz                      1683   
644                Diet Coke - 12 oz cans                      1673   
63    Muscle Milk Protein Shake Van. 11oz                      1724   
1045                  Sprite - 12 oz cans        